In [7]:
import pandas as pd
import os
from rich import print
os.chdir("/home/p289731/NWO_FrameNet/Code/football-chains-viz")

In [11]:
from ast import literal_eval

In [21]:
data = pd.read_csv(
    "data/2002829_mapped_roles.csv", index_col=0, 
    converters={"frame": literal_eval, "changed_roles": literal_eval, "unchanged_roles": literal_eval, "roles": literal_eval}
    )
print(data.shape)
data.head()

(39, 5)

frame changed_roles  \
0                 (0, 0, Draw, draw, NOUN)     [Rangers]   
1             (0, 1, Match, contest, NOUN)            []   
2  (1, 0, Competition, titleholders, NOUN)            []   
3     (1, 1, Concede_Goal, conceded, VERB)     [Rangers]   
4   (1, 2, Competition_Stage, group, NOUN)            []   

                                     unchanged_roles  \
0  [(COMPETITION_STAGE, [from, a, tight, Anglo-Sc...   
1  [(MATCH_LOCATION, [at, Old, Trafford]), (COMPE...   
2                               [(TEAM, [Scottish])]   
3  [(CONCEDING_TEAM, [they]), (GOAL, [more, goals])]   
4         [(COMPETITION, [UEFA, Champions, League])]   

                                               roles       changed_role  
0  [(COMPETITION_STAGE, [from, a, tight, Anglo-Sc...  Changed Something  
1  [(MATCH_LOCATION, [at, Old, Trafford]), (COMPE...         No Changed  
2                               [(TEAM, [Scottish])]         No Changed  
3  [(CONCEDING_TEAM, [they]), (CONCEDING_TEAM, [W...  Changed Something  
4         [(COMPETITION, [UEFA, Champions, League])]         No Changed

In [30]:
# max_roles_per_frame = 
data_ = (
    data
        .assign(sentence_idx=data["frame"].apply(lambda frame: frame[0]))
        .assign(frame_idx=data["frame"].apply(lambda frame: frame[1]))
        .assign(frame_name=data["frame"].apply(lambda frame: frame[2]))
        .assign(frame_target=data["frame"].apply(lambda frame: frame[3]))
        .drop(columns=["frame"])
)[["sentence_idx", "frame_idx", "frame_name", "frame_target", "changed_roles", "roles"]]
data_.head()


sentence_idx  frame_idx         frame_name  frame_target changed_roles  \
0             0          0               Draw          draw     [Rangers]   
1             0          1              Match       contest            []   
2             1          0        Competition  titleholders            []   
3             1          1       Concede_Goal      conceded     [Rangers]   
4             1          2  Competition_Stage         group            []   

                                               roles  
0  [(COMPETITION_STAGE, [from, a, tight, Anglo-Sc...  
1  [(MATCH_LOCATION, [at, Old, Trafford]), (COMPE...  
2                               [(TEAM, [Scottish])]  
3  [(CONCEDING_TEAM, [they]), (CONCEDING_TEAM, [W...  
4         [(COMPETITION, [UEFA, Champions, League])]

In [38]:
max_sent = max(data_["sentence_idx"])
max_frame_per_sent = data_.groupby("sentence_idx").agg({"frame_idx": max}).reset_index()
sent_to_max_frame = dict(zip(max_frame_per_sent["sentence_idx"], max_frame_per_sent["frame_idx"]))

In [64]:
data_with_time = data_.assign(
    time_point= (data_
        .apply(lambda row: (row["sentence_idx"] + row["frame_idx"] / (sent_to_max_frame[row["sentence_idx"]])) / (max_sent + 1), axis=1)
    )
)


data_with_first_roles = data_with_time.assign(
    first_role = data_with_time["changed_roles"].apply(lambda roles: roles[0] if len(roles) > 0 else None)
)

data_with_first_roles.dropna(axis=0, subset=["first_role"])

sentence_idx  frame_idx     frame_name frame_target  \
0              0          0           Draw         draw   
3              1          1   Concede_Goal     conceded   
5              1          3      Bring_Off       return   
6              1          6      Bring_Off    departing   
11             2          3        Victory      triumph   
12             2          4         Deploy     fielding   
13             2          5         Player   full-backs   
14             3          1           Draw         draw   
15             3          2           Shot          nod   
16             3          3           Pass        cross   
18             3          5     One_On_One   two-on-one   
20             3          7      Intervene        avert   
25             4          7     Being_Free     isolated   
26             4          9           Team      defence   
27             5          0        Control          got   
28             5          1           Pass        cross   
30             5          3      Challenge    challenge   
31             5          4          Field         edge   
33             5          6        Control     latching   
34             5          7           Shot       lofted   
35             5          8           Pass         ball   
36             5         10  Shot_Supports         shot   
37             5         11           Shot      whisker   

                          changed_roles  \
0                             [Rangers]   
3                             [Rangers]   
5                         [Man. United]   
6                         [Man. United]   
11                        [Man. United]   
12                            [Rangers]   
13                            [Rangers]   
14                        [Man. United]   
15                        [Man. United]   
16                        [Man. United]   
18  [Man. United, Rangers, Man. United]   
20                            [Rangers]   
25                            [Rangers]   
26                        [Man. United]   
27      [Rangers, Man. United, Rangers]   
28                            [Rangers]   
30                        [Man. United]   
31                        [Man. United]   
33                            [Rangers]   
34                        [Man. United]   
35                        [Man. United]   
36                        [Man. United]   
37                        [Man. United]   

                                                roles  time_point   first_role  
0   [(COMPETITION_STAGE, [from, a, tight, Anglo-Sc...    0.000000      Rangers  
3   [(CONCEDING_TEAM, [they]), (CONCEDING_TEAM, [W...    0.187500      Rangers  
5   [(SUBSTITUTED_PLAYER, [Antonio, Valencia]), (T...    0.229167  Man. United  
6         [(SUBSTITUTED_PLAYER, [Antonio, Valencia])]    0.291667  Man. United  
11       [(MATCH_LOCATION, [at, Leeds, United, AFC])]    0.433333  Man. United  
12  [(COACH, [his]), (PLAYER, [of, three, central,...    0.466667      Rangers  
13  [(PLAYER, [Steven, Whittaker, and, Kirk, Broad...    0.500000      Rangers  
14  [(TEAM1, [United, 's]), (MATCH_LOCATION, [at, ...    0.523810  Man. United  
15  [(MOVING_BALL, [Fabio, 's, right-wing, cross])...    0.547619  Man. United  
16    [(TARGET, [right-wing]), (PASSER, [Fabio, 's])]    0.571429  Man. United  
18  [(MOVING_BALL, [Fabio, 's, right-wing, cross])...    0.619048  Man. United  
20  [(SHOT, [the, threat]), (INTERVENING_PLAYER, [...    0.666667      Rangers  
25                     [(RECIPIENT, [Kenny, Miller])]    0.796296      Rangers  
26                             [(TEAM, [United, 's])]    0.833333  Man. United  
27  [(RECIPIENT, [Kirk, Broadfoot]), (RECIPIENT, [...    0.833333      Rangers  
28                     [(PASSER, [Steven, Naismith])]    0.846154      Rangers  
30                    [(OPPONENT_PLAYER, [Smalling])]    0.871795  Man. United  
31                                 [(TEAM, [United])]    0.884615  Man. United  
33             

In [66]:
data_with_first_roles.dropna(axis=0, subset=["first_role"])["first_role"].value_counts()

Man. United    14
Rangers         9
Name: first_role, dtype: int64

In [81]:
data_with_first_roles[data_with_first_roles["first_role"] == "Man. United"]

sentence_idx  frame_idx     frame_name frame_target  \
5              1          3      Bring_Off       return   
6              1          6      Bring_Off    departing   
11             2          3        Victory      triumph   
14             3          1           Draw         draw   
15             3          2           Shot          nod   
16             3          3           Pass        cross   
18             3          5     One_On_One   two-on-one   
26             4          9           Team      defence   
30             5          3      Challenge    challenge   
31             5          4          Field         edge   
34             5          7           Shot       lofted   
35             5          8           Pass         ball   
36             5         10  Shot_Supports         shot   
37             5         11           Shot      whisker   

                          changed_roles  \
5                         [Man. United]   
6                         [Man. United]   
11                        [Man. United]   
14                        [Man. United]   
15                        [Man. United]   
16                        [Man. United]   
18  [Man. United, Rangers, Man. United]   
26                        [Man. United]   
30                        [Man. United]   
31                        [Man. United]   
34                        [Man. United]   
35                        [Man. United]   
36                        [Man. United]   
37                        [Man. United]   

                                                roles  time_point   first_role  
5   [(SUBSTITUTED_PLAYER, [Antonio, Valencia]), (T...    0.229167  Man. United  
6         [(SUBSTITUTED_PLAYER, [Antonio, Valencia])]    0.291667  Man. United  
11       [(MATCH_LOCATION, [at, Leeds, United, AFC])]    0.433333  Man. United  
14  [(TEAM1, [United, 's]), (MATCH_LOCATION, [at, ...    0.523810  Man. United  
15  [(MOVING_BALL, [Fabio, 's, right-wing, cross])...    0.547619  Man. United  
16    [(TARGET, [right-wing]), (PASSER, [Fabio, 's])]    0.571429  Man. United  
18  [(MOVING_BALL, [Fabio, 's, right-wing, cross])...    0.619048  Man. United  
26                             [(TEAM, [United, 's])]    0.833333  Man. United  
30                    [(OPPONENT_PLAYER, [Smalling])]    0.871795  Man. United  
31                                 [(TEAM, [United])]    0.884615  Man. United  
34  [(TARGET, [over, the, top]), (SHOOTER, [Ryan, ...    0.923077  Man. United  
35  [(TARGET, [over, the, top]), (PASSER, [Ryan, G...    0.935897  Man. United  
36                              [(SHOOTER, [Gibson])]    0.961538  Man. United  
37            [(TARGET, [over]), (SHOOTER, [Gibson])]    0.974359  Man. United

In [79]:
from lxml import etree as ET
kicktionary = ET.parse("kicktionary_lu_info.xml")
frame_to_scenario = {
    lu.attrib["frame"]: lu.attrib["scenario"]
    for lu in kicktionary.xpath(".//LEXICAL-UNIT") if lu.attrib["frame"]
}
frame_to_super_scenario = {
    lu.attrib["frame"]: lu.attrib["super-scenario"]
    for lu in kicktionary.xpath(".//LEXICAL-UNIT") if lu.attrib["frame"]
}

print(frame_to_scenario)
print(frame_to_super_scenario)

{
    'Intervene': 'Shot',
    'Challenge': 'One_On_One',
    'Award_Goal': 'Goal',
    'Deny': 'One_On_One',
    'Intercept': 'Pass',
    'Shot_Supports': 'Shot',
    'Save': 'Shot',
    'Pass': 'Pass',
    'Ball_Bounce': 'Motion',
    'Mark': 'Pass',
    'Goal_Kickoff': 'Shot',
    'Finish': 'Shot',
    'Beat': 'One_On_One',
    'Offside': 'Foul',
    'Bad_Pass': 'Pass',
    'Goal': 'Goal',
    'Set_Piece': 'Foul',
    'Shot': 'Shot',
    'Player_Move_With_Ball': 'Motion',
    'Sanction': 'Foul',
    'Move': 'Move',
    'Control': 'Pass',
    'Shoot_At': 'Shot',
    'Start_End_Match': 'Match',
    'Match': 'Match',
    'Deploy': 'Lineup',
    'Start': 'Lineup',
    'Player_Move': 'Motion',
    'Elimination': 'Match',
    'Result': 'Match',
    'Bring_Off': 'Substitution',
    'Away_Game': 'Match',
    'Possession': 'State_Of_Match',
    'Pass_Combination': 'Pass',
    'Lose_Ball': 'One_On_One',
    'Defense_Shot': 'Mix-Up',
    'Receive_Card': 'Foul',
    'Victory': 'Match',
    'Supply_Pass': 'Pass',
    'Bring_On': 'Substitution',
    'Chance': 'Chance',
    'Multiple_Goals': 'Goal',
    'One_On_One': 'One_On_One',
    'Substitute': 'Substitution',
    'Own_Goal': 'Goal',
    'Convert_Chance': 'Goal',
    'Ball_Land': 'Motion',
    'Progression': 'Match',
    'Home_Game': 'Match',
    'Referee_Decision': 'Foul',
    'Concede_Goal': 'Goal',
    'Mistake': 'Mix-Up',
    'Tactics': 'State_Of_Match',
    'Foul': 'Foul',
    'Being_Free': 'Pass',
    'Lead': 'State_Of_Match',
    'Create_Chance': 'Chance',
    'Win_Compensation': 'Foul',
    'Trail': 'State_Of_Match',
    'Ball_Move': 'Motion',
    'Defeat': 'Match',
    'Dissent': 'Foul',
    'Follow_Up': 'Shot',
    'Score': 'State_Of_Match',
    'Draw': 'Match',
    'Pass_Back': 'Pass',
    'Simulation': 'Foul',
    'Miss_Goal': 'Shot',
    'Miss_Chance': 'Chance',
    'Flick_On': 'Pass',
    'Ball_Escape': 'Motion',
    'Give_Card': 'Foul',
    'Take_On': 'One_On_One',
    'Connect': 'Pass',
    'Goalkeeper_Advance': 'Motion',
    'Hit': 'Shot',
    'Advantage': 'Foul',
    'Feign': 'Shot',
    'Overcome_Goalkeeper': 'Goal',
    'Prepare_Goal': 'Goal',
    'Ball': 'Actors',
    'Spectator_Activity': 'State_Of_Match',
    'Goal_Target': 'Field',
    'Player': 'Actors',
    'Referee': 'Actors',
    'Field': 'Field',
    'Team': 'Actors',
    'Bench': 'Field',
    'Coach': 'Actors',
    'Concede_Compensation': 'Foul',
    'Match_Temporal_Subdivision': 'Match',
    'Confusion': 'Mix-up',
    'Score_Goal': 'Goal',
    'Celebrate_Goal': 'Goal',
    'Suspension': 'Lineup',
    'Spectators': 'Actors',
    'Competition_Stage': 'Competition',
    'Body_Parts': 'Actors',
    'Trick': 'One_On_One',
    'Competition': 'Competition',
    'Stadium': 'Field',
    'Match_Quality': 'State_Of_Match',
    'Ball_And_Goal': 'Shot',
    'Equipment': 'Actors',
    'Injuries': 'Foul',
    'Shot_Quality': 'Shot'
}

{
    'Intervene': 'ON_THE_PITCH',
    'Challenge': 'ON_THE_PITCH',
    'Award_Goal': 'ON_THE_PITCH',
    'Deny': 'ON_THE_PITCH',
    'Intercept': 'ON_THE_PITCH',
    'Shot_Supports': 'SUPPORTS',
    'Save': 'ON_THE_PITCH',
    'Pass': 'ON_THE_PITCH',
    'Ball_Bounce': 'ON_THE_PITCH',
    'Mark': 'ON_THE_PITCH',
    'Goal_Kickoff': 'ON_THE_PITCH',
    'Finish': 'ON_THE_PITCH',
    'Beat': 'ON_THE_PITCH',
    'Offside': 'ON_THE_PITCH',
    'Bad_Pass': 'ON_THE_PITCH',
    'Goal': 'ON_THE_PITCH',
    'Set_Piece': 'ON_THE_PITCH',
    'Shot': 'ON_THE_PITCH',
    'Player_Move_With_Ball': 'ON_THE_PITCH',
    'Sanction': 'ON_THE_PITCH',
    'Move': 'ON_THE_PITCH',
    'Control': 'ON_THE_PITCH',
    'Shoot_At': 'ON_THE_PITCH',
    'Start_End_Match': 'MATCH_IN_A_COMPETITION',
    'Match': 'MATCH_IN_A_COMPETITION',
    'Deploy': 'MATCH_IN_A_COMPETITION',
    'Start': 'MATCH_IN_A_COMPETITION',
    'Player_Move': 'ON_THE_PITCH',
    'Elimination': 'MATCH_IN_A_COMPETITION',
    'Result': 'MATCH_IN_A_COMPETITION',
    'Bring_Off': 'ON_THE_PITCH',
    'Away_Game': 'MATCH_IN_A_COMPETITION',
    'Possession': 'ON_THE_PITCH',
    'Pass_Combination': 'ON_THE_PITCH',
    'Lose_Ball': 'ON_THE_PITCH',
    'Defense_Shot': 'ON_THE_PITCH',
    'Receive_Card': 'SUPPORTS',
    'Victory': 'MATCH_IN_A_COMPETITION',
    'Supply_Pass': 'SUPPORTS',
    'Bring_On': 'ON_THE_PITCH',
    'Chance': 'ON_THE_PITCH',
    'Multiple_Goals': 'ON_THE_PITCH',
    'One_On_One': 'ON_THE_PITCH',
    'Substitute': 'ON_THE_PITCH',
    'Own_Goal': 'ON_THE_PITCH',
    'Convert_Chance': 'ON_THE_PITCH',
    'Ball_Land': 'ON_THE_PITCH',
    'Progression': 'MATCH_IN_A_COMPETITION',
    'Home_Game': 'MATCH_IN_A_COMPETITION',
    'Referee_Decision': 'ON_THE_PITCH',
    'Concede_Goal': 'SUPPORTS',
    'Mistake': 'ON_THE_PITCH',
    'Tactics': 'ON_THE_PITCH',
    'Foul': 'ON_THE_PITCH',
    'Being_Free': 'ON_THE_PITCH',
    'Lead': 'MATCH_IN_A_COMPETITION',
    'Create_Chance': 'ON_THE_PITCH',
    'Win_Compensation': 'ON_THE_PITCH',
    'Trail': 'MATCH_IN_A_COMPETITION',
    'Ball_Move': 'ON_THE_PITCH',
    'Defeat': 'MATCH_IN_A_COMPETITION',
    'Dissent': 'ON_THE_PITCH',
    'Follow_Up': 'ON_THE_PITCH',
    'Score': 'MATCH_IN_A_COMPETITION',
    'Draw': 'MATCH_IN_A_COMPETITION',
    'Pass_Back': 'ON_THE_PITCH',
    'Simulation': 'ON_THE_PITCH',
    'Miss_Goal': 'ON_THE_PITCH',
    'Miss_Chance': 'ON_THE_PITCH',
    'Flick_On': 'ON_THE_PITCH',
    'Ball_Escape': 'ON_THE_PITCH',
    'Give_Card': 'SUPPORTS',
    'Take_On': 'ON_THE_PITCH',
    'Connect': 'ON_THE_PITCH',
    'Goalkeeper_Advance': 'ON_THE_PITCH',
    'Hit': 'ON_THE_PITCH',
    'Advantage': 'ON_THE_PITCH',
    'Feign': 'ON_THE_PITCH',
    'Overcome_Goalkeeper': 'ON_THE_PITCH',
    'Prepare_Goal': 'ON_THE_PITCH',
    'Ball': 'ACTORS_AND_OBJECTS',
    'Spectator_Activity': 'ON_THE_PITCH',
    'Goal_Target': 'ACTORS_AND_OBJECTS',
    'Player': 'ACTORS_AND_OBJECTS',
    'Referee': 'ACTORS_AND_OBJECTS',
    'Field': 'ACTORS_AND_OBJECTS',
    'Team': 'ACTORS_AND_OBJECTS',
    'Bench': 'ACTORS_AND_OBJECTS',
    'Coach': 'ACTORS_AND_OBJECTS',
    'Concede_Compensation': 'ON_THE_PITCH',
    'Match_Temporal_Subdivision': 'MATCH_IN_A_COMPETITION',
    'Confusion': 'ON_THE_PITCH',
    'Score_Goal': 'ON_THE_PITCH',
    'Celebrate_Goal': 'ON_THE_PITCH',
    'Suspension': 'MATCH_IN_A_COMPETITION',
    'Spectators': 'ACTORS_AND_OBJECTS',
    'Competition_Stage': 'ACTORS_AND_OBJECTS',
    'Body_Parts': 'ACTORS_AND_OBJECTS',
    'Trick': 'ON_THE_PITCH',
    'Competition': 'ACTORS_AND_OBJECTS',
    'Stadium': 'ACTORS_AND_OBJECTS',
    'Match_Quality': 'ON_THE_PITCH',
    'Ball_And_Goal': 'ACTORS_AND_OBJECTS',
    'Equipment': 'ACTORS_AND_OBJECTS',
    'Injuries': 'ON_THE_PITCH',
    'Shot_Quality': 'ON_THE_PITCH'
}